In [54]:
!pip install datasets
from datasets import load_dataset
 
dataset = load_dataset("polyglot_ner",'de')

Reusing dataset polyglot_ner (/root/.cache/huggingface/datasets/polyglot_ner/de/1.0.0/c929318589a30ee3f0dc5d53f1f99bf25a7ec16d3f319b3b671765c5ea464c99)


In [55]:
dataset

DatasetDict({
    train: Dataset({
        features: ['id', 'lang', 'words', 'ner'],
        num_rows: 547578
    })
})

In [56]:
train1 = load_dataset("polyglot_ner",'de', split='train[0:1000]')
train2 = load_dataset("polyglot_ner",'de', split='train[1000:6000]')
eval= load_dataset("polyglot_ner",'de', split='train[5000:7000]')

Reusing dataset polyglot_ner (/root/.cache/huggingface/datasets/polyglot_ner/de/1.0.0/c929318589a30ee3f0dc5d53f1f99bf25a7ec16d3f319b3b671765c5ea464c99)
Reusing dataset polyglot_ner (/root/.cache/huggingface/datasets/polyglot_ner/de/1.0.0/c929318589a30ee3f0dc5d53f1f99bf25a7ec16d3f319b3b671765c5ea464c99)
Reusing dataset polyglot_ner (/root/.cache/huggingface/datasets/polyglot_ner/de/1.0.0/c929318589a30ee3f0dc5d53f1f99bf25a7ec16d3f319b3b671765c5ea464c99)


In [57]:
print(train1.shape)
print(train2.shape)
print(eval.shape)

(1000, 4)
(5000, 4)
(2000, 4)


In [58]:
import pandas as pd

df_train2 = pd.DataFrame(train2)
df_train2.head()

id  ...                                              words
0  1000  ...  [Inhalt, Die, Geschichte, spielt, auf, zwei, H...
1  1001  ...  [Ab, 1940, war, sie, in, der, Dachorganisation...
2  1002  ...  [Juni, 1980, in, Warschau, ), war, ein, polnis...
3  1003  ...  [Maria, Grengg, (*, 26, ., Februar, 1888, in, ...
4  1004  ...  [Innerhalb, der, Partei, engagiert, sie, sich,...

[5 rows x 4 columns]

In [59]:
import numpy as np

class SentenceGetter(object):

    def __init__(self, data):
        # self.n_sent = 1
        self.data = data
        # self.empty = False
        agg_func = lambda s: [(w,n) for w,n in zip(s["words"].values.tolist(),
                                                           s["ner"].values.tolist())]
        self.grouped = self.data.groupby("id").apply(agg_func)
        self.sentences = [s for s in self.grouped]

getter = SentenceGetter(df_train2)

sentence_arr = []
label_arr = []

for sentence in getter.sentences:
  for s in sentence:
    sentence_arr.append(s[0])
    label_arr.append(s[1])

print(sentence_arr[0], label_arr[0],  len(sentence_arr), len(label_arr))

['Inhalt', 'Die', 'Geschichte', 'spielt', 'auf', 'zwei', 'Handlungsebenen', ':', 'In', 'der', 'Binnenerzählung', 'flieht', 'die', 'junge', 'Amelia', 'Earnshawe', 'vor', 'Ghul', 'en', 'in', 'eine', 'alte', 'Villa', '.'] ['O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O'] 5000 5000


In [60]:
unique_labels = list(set(i for j in label_arr for i in j)) 
print ("Unique labels: ", unique_labels) 

Unique labels:  ['ORG', 'O', 'LOC', 'PER']


In [61]:
unique_labels.append("PAD")
tag2idx = {t: i for i, t in enumerate(unique_labels)}
tag2idx

{'LOC': 2, 'O': 1, 'ORG': 0, 'PAD': 4, 'PER': 3}

In [62]:
import torch

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
n_gpu = torch.cuda.device_count()
print('Device Name: ',torch.cuda.get_device_name(0))

Device Name:  Tesla T4


In [63]:
!pip install transformers
from transformers import BertTokenizer,BertForTokenClassification

tokenizer = BertTokenizer.from_pretrained('bert-base-cased', do_lower_case=False)

def tokenize_and_preserve_labels(sentence, text_labels):
    tokenized_sentence = []
    labels = []

    for word, label in zip(sentence, text_labels):

        # Tokenize the word and count # of subwords the word is broken into
        tokenized_word = tokenizer.tokenize(word)
        n_subwords = len(tokenized_word)

        # Add the tokenized word to the final tokenized word list
        tokenized_sentence.extend(tokenized_word)

        # Add the same label to the new list of labels `n_subwords` times
        labels.extend([label] * n_subwords)

    return tokenized_sentence, labels

tokenized_texts_and_labels = [
    tokenize_and_preserve_labels(sent, labs)
    for sent, labs in zip(sentence_arr, label_arr)
]    

tokenized_texts = [token_label_pair[0] for token_label_pair in tokenized_texts_and_labels]
labels = [token_label_pair[1] for token_label_pair in tokenized_texts_and_labels]

print("Tokenized_text, lables: ", tokenized_texts, labels)


Tokenized_text, lables:  [['In', '##halt', 'Die', 'G', '##es', '##chichte', 's', '##pie', '##lt', 'au', '##f', 'z', '##wei', 'Hand', '##lung', '##se', '##ben', '##en', ':', 'In', 'der', 'Bin', '##nen', '##er', '##z', '##ä', '##hl', '##ung', 'fl', '##ie', '##ht', 'die', 'j', '##ung', '##e', 'Amelia', 'E', '##ar', '##ns', '##haw', '##e', 'v', '##or', 'G', '##hul', 'en', 'in', 'e', '##ine', 'al', '##te', 'Villa', '.'], ['A', '##b', '1940', 'war', 'si', '##e', 'in', 'der', 'Da', '##chor', '##gan', '##isation', 'des', 't', '##sche', '##chi', '##schen', 'Wide', '##rst', '##and', '##es', 'Ú', '##VO', '##D', 've', '##rt', '##ret', '##en', '.'], ['Jun', '##i', '1980', 'in', 'Wars', '##cha', '##u', ')', 'war', 'e', '##in', 'p', '##ol', '##nis', '##cher', 'Math', '##ema', '##ti', '##ker', 'und', 'Lo', '##gi', '##ker', '.'], ['Maria', 'G', '##ren', '##gg', '(', '*', '26', '.', 'Feb', '##ru', '##ar', '1888', 'in', 'Stein', 'an', 'der', 'Don', '##au', ',', 'Ni', '##ede', '##r', '##ö', '##ster', '##r

In [64]:
from keras.preprocessing.sequence import pad_sequences

#we cut and pad the token and label sequences to our desired length.
MAX_LEN = 75
input_ids = pad_sequences([tokenizer.convert_tokens_to_ids(txt) for txt in tokenized_texts],
                          maxlen=MAX_LEN, dtype="long", value=0.0,
                          truncating="post", padding="post")

tags = pad_sequences([[tag2idx.get(l) for l in lab] for lab in labels],
                     maxlen=MAX_LEN, value=tag2idx["PAD"], padding="post",
                     dtype="long", truncating="post")

attention_masks = [[float(i != 0.0) for i in ii] for ii in input_ids]

print("Input Ids and Tags: ",input_ids, tags, attention_masks)

Input Ids and Tags:  [[ 1130 24537  5736 ...     0     0     0]
 [  138  1830  3020 ...     0     0     0]
 [12865  1182  2253 ...     0     0     0]
 ...
 [ 5736 14477 10340 ...     0     0     0]
 [ 9918 24356  1790 ...     0     0     0]
 [  146  8167  1162 ...     0     0     0]] [[1 1 1 ... 4 4 4]
 [1 1 1 ... 4 4 4]
 [1 1 1 ... 4 4 4]
 ...
 [1 1 1 ... 4 4 4]
 [1 1 1 ... 4 4 4]
 [1 1 1 ... 4 4 4]] [[1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0], [1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0

In [65]:
from sklearn.model_selection import train_test_split

tr_inputs, val_inputs, tr_tags, val_tags = train_test_split(input_ids, tags,
                                                            random_state=2018, test_size=0.1)
tr_masks, val_masks, _, _ = train_test_split(attention_masks, input_ids,
                                             random_state=2018, test_size=0.1)
#for pytorch convert the dataset to torch tensors
tr_inputs = torch.tensor(tr_inputs)
val_inputs = torch.tensor(val_inputs)
tr_tags = torch.tensor(tr_tags)
val_tags = torch.tensor(val_tags)
tr_masks = torch.tensor(tr_masks)
val_masks = torch.tensor(val_masks)

In [66]:
from torch.utils.data import TensorDataset, DataLoader, RandomSampler, SequentialSampler

bs = 32 #batch-size

train_data = TensorDataset(tr_inputs, tr_masks, tr_tags)
train_sampler = RandomSampler(train_data)
train_dataloader = DataLoader(train_data, sampler=train_sampler, batch_size=bs)

valid_data = TensorDataset(val_inputs, val_masks, val_tags)
valid_sampler = SequentialSampler(valid_data)
valid_dataloader = DataLoader(valid_data, sampler=valid_sampler, batch_size=bs)

In [67]:
from transformers import AdamW

model = BertForTokenClassification.from_pretrained(
    "bert-base-cased",
    num_labels=len(tag2idx),
    output_attentions = False,
    output_hidden_states = False
)

model.to(device)

FULL_FINETUNING = True
if FULL_FINETUNING:
    param_optimizer = list(model.named_parameters())
    no_decay = ['bias', 'gamma', 'beta']
    optimizer_grouped_parameters = [
        {'params': [p for n, p in param_optimizer if not any(nd in n for nd in no_decay)],
         'weight_decay_rate': 0.01},
        {'params': [p for n, p in param_optimizer if any(nd in n for nd in no_decay)],
         'weight_decay_rate': 0.0}
    ]
else:
    param_optimizer = list(model.classifier.named_parameters())
    optimizer_grouped_parameters = [{"params": [p for n, p in param_optimizer]}]

optimizer = AdamW(
    optimizer_grouped_parameters,
    lr=3e-5,
    eps=1e-8
)

Some weights of the model checkpoint at bert-base-cased were not used when initializing BertForTokenClassification: ['cls.predictions.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.transform.dense.bias', 'cls.predictions.decoder.weight', 'cls.seq_relationship.weight', 'cls.seq_relationship.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.LayerNorm.bias']
- This IS expected if you are initializing BertForTokenClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForTokenClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForTokenClassification were not initialized from the model checkpoint at bert-base-cas

In [68]:
from transformers import get_linear_schedule_with_warmup

epochs = 3
max_grad_norm = 1.0

# Total number of training steps is number of batches * number of epochs.
total_steps = len(train_dataloader) * epochs

# # Create the learning rate scheduler.
# scheduler = get_linear_schedule_with_warmup(
#     optimizer,
#     num_warmup_steps=0,
#     num_training_steps=total_steps
# )

In [69]:
!pip install seqeval
from seqeval.metrics import accuracy_score
from sklearn.metrics import f1_score

from tqdm import tqdm, trange


## Store the average loss after each epoch so we can plot them.
loss_values, validation_loss_values = [], []

for _ in trange(epochs, desc="Epoch"):
   #               Training
    model.train()
    # Reset the total loss for this epoch.
    total_loss = 0

    # Training loop
    for step, batch in enumerate(train_dataloader):
        # add batch to gpu
        batch = tuple(t.to(device) for t in batch)
        b_input_ids, b_input_mask, b_labels = batch
        # Always clear any previously calculated gradients before performing a backward pass.
        model.zero_grad()

        b_input_ids.to(device)

        # forward pass
        # This will return the loss (rather than the model output)
        # because we have provided the `labels`.
        outputs = model(b_input_ids, token_type_ids=None,
                        attention_mask=b_input_mask, labels=b_labels)
        # get the loss
        loss = outputs[0]
        # Perform a backward pass to calculate the gradients.
        loss.backward()
        # track train loss
        total_loss += loss.item()
        # Clip the norm of the gradient
        # This is to help prevent the "exploding gradients" problem.
        torch.nn.utils.clip_grad_norm_(parameters=model.parameters(), max_norm=max_grad_norm)
        # update parameters
        optimizer.step()
        # Update the learning rate.
        # scheduler.step()

    # Calculate the average loss over the training data.
    avg_train_loss = total_loss / len(train_dataloader)
    print("Average train loss: {}".format(avg_train_loss))

    # Store the loss value for plotting the learning curve.
    loss_values.append(avg_train_loss)


    # ========================================
    #               Validation
    # ========================================
    # After the completion of each training epoch, measure our performance on
    # our validation set.

    # Put the model into evaluation mode
    model.eval()
    # Reset the validation loss for this epoch.
    eval_loss, eval_accuracy = 0, 0
    nb_eval_steps, nb_eval_examples = 0, 0
    predictions , true_labels = [], []
    for batch in valid_dataloader:
        batch = tuple(t.to(device) for t in batch)
        b_input_ids, b_input_mask, b_labels = batch

        # Telling the model not to compute or store gradients,
        # saving memory and speeding up validation
        with torch.no_grad():
            # Forward pass, calculate logit predictions.
            # This will return the logits rather than the loss because we have not provided labels.
            outputs = model(b_input_ids, token_type_ids=None,
                            attention_mask=b_input_mask, labels=b_labels)
        # Move logits and labels to CPU
        logits = outputs[1].detach().cpu().numpy()
        label_ids = b_labels.to('cpu').numpy()

        # Calculate the accuracy for this batch of test sentences.
        eval_loss += outputs[0].mean().item()
        predictions.extend([list(p) for p in np.argmax(logits, axis=2)])
        true_labels.extend(label_ids)

    eval_loss = eval_loss / len(valid_dataloader)
    validation_loss_values.append(eval_loss)
    print("Validation loss: {}".format(eval_loss))
    pred_tags = [unique_labels[p_i] for p, l in zip(predictions, true_labels) for p_i, l_i in zip(p, l) if unique_labels[l_i] != "PAD"]
    valid_tags = [unique_labels[l_i] for l in true_labels for l_i in l if unique_labels[l_i] != "PAD"]

    print("Validation Accuracy: {}".format(accuracy_score(pred_tags, valid_tags)))
    print("Validation F1-Score Micro: {}".format(f1_score(valid_tags, pred_tags, average='micro')))
    print("Validation F1-Score Macro: {}".format(f1_score(valid_tags, pred_tags, average='macro')))
    print()













Epoch:   0%|          | 0/3 [00:00<?, ?it/s]

Average train loss: 0.21129568824742703














Epoch:  33%|███▎      | 1/3 [01:04<02:09, 64.84s/it]

Validation loss: 0.15726019255816936
Validation Accuracy: 0.9467533148157853
Validation F1-Score Micro: 0.9467533148157853
Validation F1-Score Macro: 0.5139394662624469

Average train loss: 0.12173178541005081














Epoch:  67%|██████▋   | 2/3 [02:09<01:04, 64.68s/it]

Validation loss: 0.14348802529275417
Validation Accuracy: 0.9488496410041403
Validation F1-Score Micro: 0.9488496410041403
Validation F1-Score Macro: 0.6894710853911757

Average train loss: 0.08115638097655689














Epoch: 100%|██████████| 3/3 [03:13<00:00, 64.35s/it]

Validation loss: 0.14525580639019608
Validation Accuracy: 0.9471725800534563
Validation F1-Score Micro: 0.9471725800534563
Validation F1-Score Macro: 0.6891219837923033

